In [1]:
import os
os.chdir('../')

In [2]:
from keras.models import Model
from keras.layers import Input, Dense, Reshape, merge, dot
from keras.layers.embeddings import Embedding
from keras.preprocessing.sequence import skipgrams
from keras.preprocessing import sequence

import urllib
import collections
import os
import zipfile

import numpy as np
import tensorflow as tf
import pandas as pd

Using TensorFlow backend.


In [3]:
import site; site.getsitepackages()

['/home/manishsahu-xps/miniconda3/envs/py3/lib/python3.6/site-packages']

In [4]:
from src import util
from src import pre_processing

In [5]:
import importlib
importlib.reload(pre_processing)

<module 'src.pre_processing' from '/home/manishsahu-xps/Downloads/tiler/word2vec_keras/src/pre_processing.py'>

In [6]:
physical_devices = tf.config.experimental.list_physical_devices('GPU')
assert len(physical_devices) > 0, "Not enough GPU hardware devices available"
_config = tf.config.experimental.set_memory_growth(physical_devices[0], True)

AssertionError: Not enough GPU hardware devices available

In [7]:
tf.config.experimental.list_physical_devices('GPU')

[]

In [8]:
path_data = 'data/reviews.csv'

In [9]:
data = pd.read_csv(path_data)

In [10]:
data.head(3)

listing_id    id        date  reviewer_id reviewer_name  \
0        2818  1191  2009-03-30        10952           Lam   
1        2818  1771  2009-04-24        12798         Alice   
2        2818  1989  2009-05-03        11869       Natalja   

                                            comments  
0  Daniel is really cool. The place was nice and ...  
1  Daniel is the most amazing host! His place is ...  
2  We had such a great time in Amsterdam. Daniel ...

In [11]:
text = list(data['text'].values)

In [12]:
len(text)

941009

In [13]:
text = ''.join(text)

In [15]:
n = len(text.split(' '))
print(f'Number of words: {n}')

Number of words: 10814901


In [16]:
text[0:250]

'Attempt missed. Mladen Petric (Hamburg) left footed shot from the left side of the box is high and wide to the left. Assisted by Gokhan Tore.Corner,  Borussia Dortmund. Conceded by Dennis Diekmeier.Corner,  Borussia Dortmund. Conceded by Heiko Wester'

In [17]:
text_processed = pre_processing.preprocess_str(text)

In [18]:
text_processed[:250]

'attempt missed mladen petric ( hamburg ) left footed shot from the left side of the box is high and wide to the left assisted by gokhan tore corner borussia dortmund conceded by dennis diekmeier corner borussia dortmund conceded by heiko westermann f'

In [17]:
def build_dataset(words, n_words):
    """Process raw inputs into a dataset."""
    count = [['UNK', -1]]
    count.extend(collections.Counter(words).most_common(n_words - 1))
    dictionary = dict()
    for word, _ in count:
        dictionary[word] = len(dictionary)
    data = list()
    unk_count = 0
    for word in words:
        if word in dictionary:
            index = dictionary[word]
        else:
            index = 0  # dictionary['UNK']
            unk_count += 1
        data.append(index)
    count[0][1] = unk_count
    reversed_dictionary = dict(zip(dictionary.values(), dictionary.keys()))
    return data, count, dictionary, reversed_dictionary

In [18]:
words = text_processed.split()
n_words = 5000 # Vocab size

In [19]:
vocab_size = n_words
data, count, dictionary, reversed_dictionary = build_dataset(words, n_words)
print(data[:7])

[15, 29, 3323, 3141, 2, 295, 3]


In [20]:
window_size = 3
vector_dim = 100
epochs = 20000

valid_size = 16     # Random set of words to evaluate similarity on.
valid_window = 100  # Only pick dev samples in the head of the distribution.
valid_examples = np.random.choice(valid_window, valid_size, replace=False)


In [21]:
sampling_table = sequence.make_sampling_table(vocab_size)

In [22]:
sampling_table

array([0.00315225, 0.00315225, 0.00547597, ..., 0.67410077, 0.67417563,
       0.67425049])

In [23]:
len(sampling_table), len(dictionary)

(5000, 5000)

In [24]:
couples, labels = skipgrams(data, vocab_size, window_size=window_size, sampling_table=sampling_table)
word_target, word_context = zip(*couples)
word_target = np.array(word_target, dtype="int32")
word_context = np.array(word_context, dtype="int32")

print(couples[:10], labels[:10])


[[966, 1932], [875, 2], [134, 3272], [6, 60], [2065, 38], [66, 4308], [238, 3366], [468, 2], [697, 3608], [3134, 4182]] [0, 1, 0, 1, 1, 0, 0, 1, 0, 0]


In [25]:
reversed_dictionary[couples[0][0]], reversed_dictionary[couples[0][1]]

('perisic', 'pawel')

In [26]:
couples[:10]

[[966, 1932],
 [875, 2],
 [134, 3272],
 [6, 60],
 [2065, 38],
 [66, 4308],
 [238, 3366],
 [468, 2],
 [697, 3608],
 [3134, 4182]]

In [34]:
dot([target, context], normalize=False, dot_axes=0)

TypeError: 'module' object is not callable

In [46]:

# create some input variables
input_target = Input((1,))
input_context = Input((1,))

embedding = Embedding(vocab_size, vector_dim, input_length=1, name='embedding')
target = embedding(input_target)
target = Reshape((vector_dim, 1))(target)
context = embedding(input_context)
context = Reshape((vector_dim, 1))(context)

# setup a cosine similarity operation which will be output in a secondary model

similarity = dot([target, context], normalize=False, axes=1)

# now perform the dot product operation to get a similarity measure
dot_product = dot([target, context], normalize=True, axes=1)
dot_product = Reshape((1,))(dot_product)
# add the sigmoid output layer
output = Dense(1, activation='sigmoid')(dot_product)
# create the primary training model
model = Model(input=[input_target, input_context], output=output)
model.compile(loss='binary_crossentropy', optimizer='adam', )


/home/manishpc/miniconda3/envs/py3/lib/python3.6/site-packages/ipykernel_launcher.py:21: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=[<tf.Tenso..., outputs=Tensor("de...)`


In [47]:
model.summary()

Model: "model_4"
__________________________________________________________________________________________________
Layer (type)                    Output Shape         Param #     Connected to                     
input_19 (InputLayer)           (None, 1)            0                                            
__________________________________________________________________________________________________
input_20 (InputLayer)           (None, 1)            0                                            
__________________________________________________________________________________________________
embedding (Embedding)           (None, 1, 100)       500000      input_19[0][0]                   
                                                                 input_20[0][0]                   
__________________________________________________________________________________________________
reshape_21 (Reshape)            (None, 100, 1)       0           embedding[0][0]            

In [48]:

# create a secondary validation model to run our similarity checks during training
validation_model = Model(input=[input_target, input_context], output=similarity)


/home/manishpc/miniconda3/envs/py3/lib/python3.6/site-packages/ipykernel_launcher.py:2: UserWarning: Update your `Model` call to the Keras 2 API: `Model(inputs=[<tf.Tenso..., outputs=Tensor("do...)`
  


In [62]:


class SimilarityCallback:
    def run_sim(self):
        near_word = [dictionary['messi'], dictionary['ronaldo']]
        for i in range(2):
            valid_word = reversed_dictionary[near_word[i]]
            top_k = 8  # number of nearest neighbors
            sim = self._get_sim(valid_examples[i])
            nearest = (-sim).argsort()[1:top_k + 1]
            log_str = 'Nearest to %s:' % valid_word
            for k in range(top_k):
                close_word = reversed_dictionary[nearest[k]]
                log_str = '%s %s,' % (log_str, close_word)
            print(log_str)

    @staticmethod
    def _get_sim(valid_word_idx):
        sim = np.zeros((vocab_size,))
        in_arr1 = np.zeros((1,))
        in_arr2 = np.zeros((1,))
        in_arr1[0,] = valid_word_idx
        for i in range(vocab_size):
            in_arr2[0,] = i
            out = validation_model.predict_on_batch([in_arr1, in_arr2])
            sim[i] = out
        return sim
sim_cb = SimilarityCallback()

arr_1 = np.zeros((1,))
arr_2 = np.zeros((1,))
arr_3 = np.zeros((1,))
for cnt in range(epochs):
    idx = np.random.randint(0, len(labels)-1)
    arr_1[0,] = word_target[idx]
    arr_2[0,] = word_context[idx]
    arr_3[0,] = labels[idx]
    loss = model.fit([arr_1, arr_2], arr_3, 
                     epochs=epochs)
    if cnt % 100 == 0:
        print("Iteration {}, loss={}".format(cnt, loss))
    if cnt % 10000 == 0:
        sim_cb.run_sim()

Epoch 1/20000
1/1 [==============================] - 0s 13ms/step - loss: 0.3230
Epoch 2/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.2233
Epoch 3/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.1353
Epoch 4/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0782
Epoch 5/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0458
Epoch 6/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0284
Epoch 7/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0188
Epoch 8/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0133
Epoch 9/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0100
Epoch 10/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0080
Epoch 11/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0066
Epoch 12/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0057
Epoch 13/20000
1/1 [================

Epoch 103/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 104/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 105/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 106/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0022
Epoch 107/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 108/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 109/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 110/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 111/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0022
Epoch 112/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0021
Epoch 113/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0021
Epoch 114/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0021
Epoch 115/20000


Epoch 203/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0020
Epoch 204/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0020
Epoch 205/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0020
Epoch 206/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0020
Epoch 207/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0020
Epoch 208/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0020
Epoch 209/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0020
Epoch 210/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0020
Epoch 211/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0020
Epoch 212/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0020
Epoch 213/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0020
Epoch 214/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0020
Epoch 215/20000


Epoch 303/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 304/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 305/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 306/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 307/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 308/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 309/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 310/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 311/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 312/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 313/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 314/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 315/20000


Epoch 403/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 404/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 405/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 406/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 407/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 408/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 409/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 410/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 411/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 412/20000
1/1 [==============================] - 0s 3ms/step - loss: 0.0019
Epoch 413/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 414/20000
1/1 [==============================] - 0s 2ms/step - loss: 0.0019
Epoch 415/20000


...

1/1 [==============================] - 0s 2ms/step - loss: 2.7486e-07
Epoch 16541/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.7476e-07
Epoch 16542/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.7467e-07
Epoch 16543/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.7457e-07
Epoch 16544/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.7447e-07
Epoch 16545/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.7437e-07
Epoch 16546/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.7427e-07
Epoch 16547/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.7417e-07
Epoch 16548/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.7407e-07
Epoch 16549/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.7398e-07
Epoch 16550/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.7388e-07
Epoch 16551/20000
1/1 [===========================

Epoch 16634/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6596e-07
Epoch 16635/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6588e-07
Epoch 16636/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6580e-07
Epoch 16637/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6572e-07
Epoch 16638/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6564e-07
Epoch 16639/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6556e-07
Epoch 16640/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6548e-07
Epoch 16641/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6540e-07
Epoch 16642/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6532e-07
Epoch 16643/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.6524e-07
Epoch 16644/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.6516e-07
Epoch 16645/20000
1/1 [=========

1/1 [==============================] - 0s 2ms/step - loss: 2.5862e-07
Epoch 16728/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5854e-07
Epoch 16729/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5847e-07
Epoch 16730/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5839e-07
Epoch 16731/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5831e-07
Epoch 16732/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5823e-07
Epoch 16733/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5815e-07
Epoch 16734/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5807e-07
Epoch 16735/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.5799e-07
Epoch 16736/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5791e-07
Epoch 16737/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5783e-07
Epoch 16738/20000
1/1 [===========================

Epoch 16821/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5120e-07
Epoch 16822/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5112e-07
Epoch 16823/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5104e-07
Epoch 16824/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5097e-07
Epoch 16825/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5089e-07
Epoch 16826/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5081e-07
Epoch 16827/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5073e-07
Epoch 16828/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.5065e-07
Epoch 16829/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.5057e-07
Epoch 16830/20000
1/1 [==============================] - 0s 2ms/step - loss: 2.5049e-07
Epoch 16831/20000
1/1 [==============================] - 0s 3ms/step - loss: 2.5041e-07
Epoch 16832/20000
1/1 [=========

KeyboardInterrupt: 

In [70]:
class SimilarityCallback:
    def run_sim(self):
        near_word = [dictionary['borussia'], dictionary['manchester']]
        for i in range(2):
            valid_word = reversed_dictionary[near_word[i]]
            top_k = 8  # number of nearest neighbors
            sim = self._get_sim(valid_examples[i])
            nearest = (-sim).argsort()[1:top_k + 1]
            log_str = 'Nearest to %s:' % valid_word
            for k in range(top_k):
                close_word = reversed_dictionary[nearest[k]]
                log_str = '%s %s,' % (log_str, close_word)
            print(log_str)

    @staticmethod
    def _get_sim(valid_word_idx):
        sim = np.zeros((vocab_size,))
        in_arr1 = np.zeros((1,))
        in_arr2 = np.zeros((1,))
        in_arr1[0,] = valid_word_idx
        for i in range(vocab_size):
            in_arr2[0,] = i
            out = validation_model.predict_on_batch([in_arr1, in_arr2])
            sim[i] = out
        return sim
sim_cb = SimilarityCallback()


In [71]:
sim_cb.run_sim()

Nearest to borussia: top, on, city, is, club, santiago, sane, ),
Nearest to manchester: club, antonio, marta, free, rdoba, m, united, munchen,


In [14]:
import torch
import tensorflow as tf

In [48]:
x1 = tf.constant([[1, 0, 1, 1], [1, 0, 1, 1]], dtype=float)
x2 = tf.constant([[1, 2, 2, 1], [1, 2, 2, 1]], dtype=float)

In [58]:
m = tf.keras.layers.Dot(axes=1, normalize=True)

In [59]:
m([x1, x2])

<tf.Tensor: shape=(2, 1), dtype=float32, numpy=
array([[0.73029673],
       [0.73029673]], dtype=float32)>

In [57]:
tf.keras.layers.dot([x1, x2], axes=0)

ValueError: Cannot perform batch_dot over axis 0. If your inputs are not batched, add a dummy batch dimension to your inputs using K.expand_dims(x, 0)

In [ ]:
inputs, axes, normalize=False